In [1]:
import pandas as pd
import matplotlib.pyplot as plt
plt.rc('font', family='AppleGothic')

In [2]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
import lightgbm as lgb
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt

In [3]:
df = pd.read_csv('./data/no_NaN_dataset.csv', encoding='utf-8')

In [4]:
data = df

In [5]:
use_cols = ['총인구수(명)', '유치원 수', '초등학교 수', '출생건수', '사망건수', '혼인건수', '이혼건수', '순이동', '학령인구(명)']

In [6]:
df['행정구역'] = df['행정구역(시도)'].astype(str) + ' ' + df['행정구역(시군구)'].astype(str)

In [7]:
df

행정구역(시도) 행정구역(시군구)    연도   총인구수(명)  총인구수증감    총인구수증감률  유치원 수  초등학교 수  \
0       서울특별시       종로구  2013  160070.0 -5137.0  -3.109432   17.0    14.0   
1       서울특별시        중구  2013  130465.0 -2895.0 -44.009562   13.0    12.0   
2       서울특별시       용산구  2013  239740.0 -3492.0  -1.435666   17.0    15.0   
3       서울특별시       성동구  2013  299337.0  -267.0  -0.089118   29.0    20.0   
4       서울특별시       광진구  2013  368927.0 -2386.0  -0.642585   38.0    22.0   
...       ...       ...   ...       ...     ...        ...    ...     ...   
1818     경상남도       함양군  2020   39080.0  -557.0  -1.405253   12.0    13.0   
1819     경상남도       거창군  2020   61502.0  -677.0  -1.088792   16.0    17.0   
1820     경상남도       합천군  2020   44006.0 -1198.0  -2.650208   15.0    17.0   
1821  제주특별자치도       제주시  2020  492466.0  3061.0   0.625453   78.0    68.0   
1822  제주특별자치도      서귀포시  2020  182169.0   585.0   0.322165   45.0    45.0   

        출생건수    사망건수    혼인건수    이혼건수     순이동  학령인구(명)   학령인구증감률  지가 변동률  \
0      873.0   840.0   877.0   348.0 -5331.0  25113.0 -5.763819   1.201   
1     1022.0   685.0   860.0   320.0 -3317.0  17356.0 -5.318859   0.604   
2     2129.0  1058.0  1795.0   450.0 -4688.0  34734.0 -3.180488  -2.113   
3     2838.0  1294.0  2432.0   613.0 -1957.0  46055.0 -3.052310   0.277   
4     2990.0  1331.0  2685.0   743.0 -4362.0  60341.0 -4.156739   0.454   
...      ...     ...     ...     ...     ...      ...       ...     ...   
1818   105.0   558.0    81.0    77.0  -107.0   4611.0 -4.711717   0.949   
1819   238.0   713.0   168.0   109.0  -211.0   9194.0 -1.962039   1.401   
1820   107.0   735.0    82.0    86.0  -581.0   3978.0 -7.359106   1.621   
1821  3075.0  2715.0  2214.0  1266.0  2506.0  87778.0 -1.002628  -1.724   
1822   914.0  1237.0   767.0   478.0   872.0  28418.0 -0.193165  -2.261   

              행정구역  
0        서울특별시 종로구  
1         서울특별시 중구  
2        서울특별시 용산구  
3        서울특별시 성동구  
4        서울특별시 광진구  
...            ...  
1818      경상남도 함양군  
1819      경상남도 거창군  
1820      경상남도 합천군  
1821   제주특별자치도 제주시  
1822  제주특별자치도 서귀포시  

[1823 rows x 17 columns]

In [8]:
for region in df['행정구역'].unique().tolist():
    temp_df = df[df['행정구역'] == region]

    if len(temp_df) != 8:
        print(region)

인천광역시 남구
충청북도 청주시
충청북도 청원군
대구광역시 동구
대구광역시 남구
경기도 여주시
인천광역시 미추홀구


In [9]:
drop_list = ['인천광역시 남구',
             '충청북도 청주시',
             '충청북도 청원군',
             '대구광역시 동구',
             '대구광역시 남구',
             '경기도 여주시',
             '인천광역시 미추홀구']

In [10]:
for region in drop_list:
    df = df[df['행정구역'] != region]

In [11]:
df

행정구역(시도) 행정구역(시군구)    연도   총인구수(명)  총인구수증감    총인구수증감률  유치원 수  초등학교 수  \
0       서울특별시       종로구  2013  160070.0 -5137.0  -3.109432   17.0    14.0   
1       서울특별시        중구  2013  130465.0 -2895.0 -44.009562   13.0    12.0   
2       서울특별시       용산구  2013  239740.0 -3492.0  -1.435666   17.0    15.0   
3       서울특별시       성동구  2013  299337.0  -267.0  -0.089118   29.0    20.0   
4       서울특별시       광진구  2013  368927.0 -2386.0  -0.642585   38.0    22.0   
...       ...       ...   ...       ...     ...        ...    ...     ...   
1818     경상남도       함양군  2020   39080.0  -557.0  -1.405253   12.0    13.0   
1819     경상남도       거창군  2020   61502.0  -677.0  -1.088792   16.0    17.0   
1820     경상남도       합천군  2020   44006.0 -1198.0  -2.650208   15.0    17.0   
1821  제주특별자치도       제주시  2020  492466.0  3061.0   0.625453   78.0    68.0   
1822  제주특별자치도      서귀포시  2020  182169.0   585.0   0.322165   45.0    45.0   

        출생건수    사망건수    혼인건수    이혼건수     순이동  학령인구(명)   학령인구증감률  지가 변동률  \
0      873.0   840.0   877.0   348.0 -5331.0  25113.0 -5.763819   1.201   
1     1022.0   685.0   860.0   320.0 -3317.0  17356.0 -5.318859   0.604   
2     2129.0  1058.0  1795.0   450.0 -4688.0  34734.0 -3.180488  -2.113   
3     2838.0  1294.0  2432.0   613.0 -1957.0  46055.0 -3.052310   0.277   
4     2990.0  1331.0  2685.0   743.0 -4362.0  60341.0 -4.156739   0.454   
...      ...     ...     ...     ...     ...      ...       ...     ...   
1818   105.0   558.0    81.0    77.0  -107.0   4611.0 -4.711717   0.949   
1819   238.0   713.0   168.0   109.0  -211.0   9194.0 -1.962039   1.401   
1820   107.0   735.0    82.0    86.0  -581.0   3978.0 -7.359106   1.621   
1821  3075.0  2715.0  2214.0  1266.0  2506.0  87778.0 -1.002628  -1.724   
1822   914.0  1237.0   767.0   478.0   872.0  28418.0 -0.193165  -2.261   

              행정구역  
0        서울특별시 종로구  
1         서울특별시 중구  
2        서울특별시 용산구  
3        서울특별시 성동구  
4        서울특별시 광진구  
...            ...  
1818      경상남도 함양군  
1819      경상남도 거창군  
1820      경상남도 합천군  
1821   제주특별자치도 제주시  
1822  제주특별자치도 서귀포시  

[1792 rows x 17 columns]

In [12]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from statsmodels.tsa.arima.model import ARIMA

def forecasting_features(data):
    sido = data['행정구역(시도)'].unique().tolist()[0]
    sigungu = data['행정구역(시군구)'].unique().tolist()[0]
    sido_sigungu = sido + ' ' + sigungu
    year = data['연도'].unique().tolist()[-1]

    future_data = {'행정구역(시도)': np.array([sido for i in range(10)]), '행정구역(시군구)': np.array([sigungu for i in range(10)]), '행정구역': np.array([sido_sigungu for i in range(10)]), '연도': np.array([i for i in range(year+1, year+11)])}

    for col in data.columns:
        if col in ('행정구역(시도)', '행정구역(시군구)', '행정구역', '연도'):
            continue
        else:
            value = data[col]
            # 시계열 데이터로 변환
            time_series = pd.Series(value)

            # ARIMA 모델 생성 및 훈련
            order = (1, 1, 1)  # (p, d, q)
            model = ARIMA(time_series, order=order)
            results = model.fit()

            # 예측
            forecast_steps = 10
            forecast = results.get_forecast(steps=forecast_steps)

            # 예측 결과 및 신뢰 구간 출력
            forecast_mean = forecast.predicted_mean
            confidence_interval = forecast.conf_int()

            if col not in ('총인구수증감률', '학령인구증감률', '지가변동률'):
                forecast_mean = forecast_mean.round()
            future_data[col] = forecast_mean
    return future_data

In [13]:
for region in df['행정구역'].unique().tolist():
    temp_df = df[df['행정구역'] == region]

    print(region)
    future_data = forecasting_features(temp_df)
    future_df = pd.DataFrame(future_data)
    df = pd.concat([df, future_df])

서울특별시 종로구


/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/Users/leebeomsu/Desktop/DShackathon/ven

서울특별시 중구


/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:836: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._i

서울특별시 용산구


...

/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:836: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._i

제주특별자치도 제주시


/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:836: FutureWarning: No supported index is available. In the next version, calling this method in a model without a supported index will result in an exception.
  return get_prediction_index(
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. fo

제주특별자치도 서귀포시


/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
/Users/leebeomsu/Desktop/DShackathon/venv/lib/python3.9/site-packages/statsmodels/tsa/base/tsa_model.py:836: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
/Users/leebeomsu/Desktop/DShackathon/ven

In [14]:
df.sort_values(by=['행정구역', '연도'], inplace=True)

In [15]:
df

행정구역(시도) 행정구역(시군구)    연도   총인구수(명)  총인구수증감   총인구수증감률  유치원 수  초등학교 수  \
105   강원특별자치도       강릉시  2013  216806.0  -935.0 -0.429409   40.0    35.0   
335   강원특별자치도       강릉시  2014  215807.0  -999.0 -0.460781   41.0    35.0   
564   강원특별자치도       강릉시  2015  214560.0 -1247.0 -0.577831   44.0    35.0   
792   강원특별자치도       강릉시  2016  213846.0  -714.0 -0.332774   38.0    35.0   
1020  강원특별자치도       강릉시  2017  213952.0   106.0  0.049568   38.0    35.0   
...       ...       ...   ...       ...     ...       ...    ...     ...   
13       충청북도       충주시  2026  210136.0   218.0  0.109523   44.0    35.0   
14       충청북도       충주시  2027  209912.0   218.0  0.109523   44.0    35.0   
15       충청북도       충주시  2028  210123.0   218.0  0.109523   44.0    35.0   
16       충청북도       충주시  2029  209924.0   218.0  0.109523   44.0    35.0   
17       충청북도       충주시  2030  210111.0   218.0  0.109523   44.0    35.0   

        출생건수    사망건수    혼인건수   이혼건수     순이동  학령인구(명)   학령인구증감률  지가 변동률  \
105   1460.0  1471.0  1026.0  528.0  -942.0  40758.0 -1.998125   1.514   
335   1298.0  1539.0   983.0  473.0  -810.0  39345.0 -3.466804   1.739   
564   1402.0  1553.0   977.0  481.0 -1185.0  37605.0 -4.422417   2.787   
792   1236.0  1545.0   920.0  465.0  -497.0  36113.0 -3.967558   2.626   
1020  1084.0  1529.0   924.0  444.0   540.0  34780.0 -3.691192   4.070   
...      ...     ...     ...    ...     ...      ...       ...     ...   
13     723.0  1696.0   823.0  489.0   423.0  30569.0 -3.303216   2.000   
14     670.0  1696.0   823.0  490.0   423.0  30563.0 -3.303203   2.000   
15     617.0  1696.0   823.0  490.0   423.0  30569.0 -3.303205   2.000   
16     564.0  1696.0   823.0  490.0   423.0  30563.0 -3.303204   2.000   
17     511.0  1696.0   823.0  490.0   423.0  30569.0 -3.303205   2.000   

             행정구역  
105   강원특별자치도 강릉시  
335   강원특별자치도 강릉시  
564   강원특별자치도 강릉시  
792   강원특별자치도 강릉시  
1020  강원특별자치도 강릉시  
...           ...  
13       충청북도 충주시  
14       충청북도 충주시  
15       충청북도 충주시  
16       충청북도 충주시  
17       충청북도 충주시  

[4032 rows x 17 columns]

In [16]:
df.to_csv('./data/forecasting_dataset(2013-2030).csv', encoding='utf-8', index=False)